In [1]:
import numpy as np
import pandas as pd
import tensorflow as tf
import os
from PIL import Image

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense
from tensorflow.keras.preprocessing.image import img_to_array, load_img,ImageDataGenerator
from tensorflow.keras.utils import to_categorical

from sklearn.model_selection import train_test_split



/tmp/ipykernel_1303038/4005904820.py:2: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd
2024-02-21 22:58:57.259970: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-02-21 22:58:57.489876: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-02-21 22:

In [2]:
txt = pd.read_csv('train.txt')
txt.head(5)

379 1e64990d1b40c1758a2aaa9c7f7a85_jumbo.jpeg negative cohen
0  379 7223b8ad031187d9a142d7f7ca02c9_jumbo.jpeg ...          
1  380 3392dc7d262e28423caca517f98c2e_jumbo.jpeg ...          
2  380 ec3a480c0926ded74429df416cfb05_jumbo.jpeg ...          
3  382 a72aeb349a63c79ed24e473c434efe_jumbo.jpg n...          
4  382 ba45a47c3ef5060ec39891046be7ca_jumbo.jpg n...

In [3]:
import csv
import re

def separate_values(row):
    # Use regular expression to find either commas or spaces as separators
    values = re.split(r' ', row)
    return values

input_csv_file = 'train.txt'
output_csv_file = 'train.csv'

with open(input_csv_file, 'r') as input_file, open(output_csv_file, 'w', newline='') as output_file:
    reader = csv.reader(input_file)
    writer = csv.writer(output_file)

    for row in reader:
        # Process each row and separate values
        separated_values = separate_values(row[0])
        
        # Write the separated values to the new CSV file
        writer.writerow(separated_values)


In [4]:
train = pd.read_csv('train.csv',header= None , names=["ID", "Img", "Class", "Ukw"])
train.sort_values(by='ID',ascending= False)
train.head(5)

ID                                        Img     Class    Ukw
0  379  1e64990d1b40c1758a2aaa9c7f7a85_jumbo.jpeg  negative  cohen
1  379  7223b8ad031187d9a142d7f7ca02c9_jumbo.jpeg  negative  cohen
2  380  3392dc7d262e28423caca517f98c2e_jumbo.jpeg  negative  cohen
3  380  ec3a480c0926ded74429df416cfb05_jumbo.jpeg  negative  cohen
4  382   a72aeb349a63c79ed24e473c434efe_jumbo.jpg  negative  cohen

In [5]:
print("Ukw:", train['Ukw'].unique(),'\n',"Class:" ,train['Class'].unique())

Ukw: ['cohen' 'actmed' 'fig1' 'sirm' 'ricord' 'rsna' 'stonybrook' 'bimcv'] 
 Class: ['negative' 'positive']


In [6]:
train.to_csv('train.csv', index=False)

In [7]:
names = []
for dirname, dirnames, filenames in os.walk('./train'):
   for filename in filenames:
       if filename.endswith(('png','jpeg','jpg')):
           names.append(filename)
           
#From image folder

In [8]:
names

['A808584-01-23-1901-NA-CHEST_AP_VIEWONLY-51610-4.000000-AP-81872-1-1.jpg',
 'sub-S314947_ses-E53559_run-1_bp-chest_vp-pa_dx-corrected.png',
 'A775003-01-11-1901-NA-CHEST_AP_PORT-30764-6.000000-AP-09806-1-1.jpg',
 'sub-S321602_ses-E64234_run-1_bp-chest_vp-pa_cr-corrected.png',
 '13fce2c5-6834-485f-8280-c3b0c1b952b5.png',
 'sub-S308861_ses-E28712_run-1_bp-chest_vp-pa_cr-corrected.png',
 'covid-19-pneumonia-58-day-7.jpg',
 'A117394-10-14-1900-NA-CHEST_AP_PORT-56188-2.000000-AP-81719-1-1.jpg',
 'A550018-12-25-1900-NA-CHEST_AP_PORT-50885-2.000000-AP-45041-1-1.jpg',
 'b163a08c-8dba-409a-b2d6-e30047625970.png',
 'sub-S321256_ses-E43289_run-1_bp-chest_vp-pa_dx-corrected.png',
 '6f3953f5-5129-4a74-b8f9-cf386f919930.png',
 'A402838-12-31-1900-NA-CHEST_AP_PORT-35179-1.000000-AP-55941-1-1.jpg',
 '06b64e36-9e61-4865-bfe4-d96eef86548c.png',
 'sub-S325701_ses-E65755_run-1_bp-chest_cr-corrected.png',
 'sub-S325150_ses-E50571_run-1_bp-chest_vp-pa_dx-corrected.png',
 'dd4682f7-2a7b-4687-b7b7-ce9e62fa7b

In [9]:
names1 = []
file = open('train.csv')
lns = csv.reader(file)
for line in lns:
    nam = line [1]
    names1.append(nam)

#From CSV file

In [10]:
names1

['Img',
 '1e64990d1b40c1758a2aaa9c7f7a85_jumbo.jpeg',
 '7223b8ad031187d9a142d7f7ca02c9_jumbo.jpeg',
 '3392dc7d262e28423caca517f98c2e_jumbo.jpeg',
 'ec3a480c0926ded74429df416cfb05_jumbo.jpeg',
 'a72aeb349a63c79ed24e473c434efe_jumbo.jpg',
 'ba45a47c3ef5060ec39891046be7ca_jumbo.jpg',
 '6f36c4ad54047bc52b38fd8c9d1e22_jumbo.jpg',
 '621f53af15cf08e6e13cb6812eead9_jumbo.jpg',
 '6646071b.jpg',
 '5359825d.jpg',
 '0cd9fcb6.jpg',
 'ce09cfab.jpg',
 'b0500187.jpg',
 '40f355ec.jpg',
 'e6eaadf0.jpg',
 '34d999a9.jpg',
 'fbb18dc0.jpg',
 '54d57e77.jpg',
 'a7e0a141.jpg',
 'd806f9a1.jpg',
 '19a01707.jpg',
 'bf551b8b.jpg',
 '1e534853.jpg',
 'aa9655de.jpg',
 '073a8f93.jpg',
 '7a9ec606.jpg',
 '88859dc1.jpg',
 '3a81faf3.jpg',
 'bcb814aa.jpg',
 '76093afc.jpg',
 '000012.jpg',
 '16755_1_1.jpg',
 '000001-1.jpg',
 '000001-3.jpg',
 '000003-1.jpg',
 '000003-2.jpg',
 '000001-4.jpg',
 '000002-3.jpg',
 '000003-3.jpg',
 '000001-6.jpg',
 '000002-4.jpg',
 '000001-7.jpg',
 '000003-4.jpg',
 '000001-8.jpg',
 '000002-5.jpg',


In [11]:
print(len(names), len(names1))

67862 67864


In [12]:
import csv
from PIL import Image

def compare_column_with_images(csv_file, column_index, image_folder):
    # Open the CSV file
    with open(csv_file, 'r') as file:
        reader = csv.reader(file)
        
        # Iterate through each row
        for row in reader:
            try:
                # Extract the image name from the specified column
                image_name = row[column_index]
                
                # Construct the full path to the image file
                image_path = f"{image_folder}/{image_name}"
                
                # Open the image using Pillow
                image = Image.open(image_path)
                
                # Perform image processing or comparison as needed
                # For example, you can get image dimensions:
                width, height = image.size
                print(f"Image '{image_name}' has dimensions: {width} x {height}")
                
            except Exception as e:
                print(f"Error processing row: {row}, Error: {e}")
        print(" All is well ")
# Example usage
csv_file = 'train.csv'
column_index = 1  # Adjust to the index of the column you want to compare
image_folder = 'train'

compare_column_with_images(csv_file, column_index, image_folder)


Error processing row: ['ID', 'Img', 'Class', 'Ukw'], Error: [Errno 2] No such file or directory: 'train/Img'
Image '1e64990d1b40c1758a2aaa9c7f7a85_jumbo.jpeg' has dimensions: 1024 x 912
Image '7223b8ad031187d9a142d7f7ca02c9_jumbo.jpeg' has dimensions: 1024 x 952
Image '3392dc7d262e28423caca517f98c2e_jumbo.jpeg' has dimensions: 977 x 1024
Image 'ec3a480c0926ded74429df416cfb05_jumbo.jpeg' has dimensions: 1024 x 902
Image 'a72aeb349a63c79ed24e473c434efe_jumbo.jpg' has dimensions: 1024 x 1024
Image 'ba45a47c3ef5060ec39891046be7ca_jumbo.jpg' has dimensions: 932 x 1024
Image '6f36c4ad54047bc52b38fd8c9d1e22_jumbo.jpg' has dimensions: 795 x 1024
Image '621f53af15cf08e6e13cb6812eead9_jumbo.jpg' has dimensions: 837 x 1024
Image '6646071b.jpg' has dimensions: 1024 x 1024
Image '5359825d.jpg' has dimensions: 1024 x 1024
Image '0cd9fcb6.jpg' has dimensions: 1024 x 1024
Image 'ce09cfab.jpg' has dimensions: 1024 x 1024
Image 'b0500187.jpg' has dimensions: 1024 x 1024
Image '40f355ec.jpg' has dimensio

In [13]:
import pandas as pd
import os
from PIL import Image
from shutil import move

def separate_image_sets(csv_file, image_folder, output_folder):
    # Read the CSV file into a pandas DataFrame
    df = pd.read_csv(csv_file)
    
    # Iterate through each row
    for index, row in df.iterrows():
        try:
            # Extract the image name and class label from the DataFrame
            image_name = row['Img']  # Replace 'image_name_column' with the actual column name
            class_label = row['Class']  # Assuming 'Class' is the column containing class labels
            
            # Construct the full path to the image file
            image_path = os.path.join(image_folder, image_name)
            
            # Open the image using Pillow
            image = Image.open(image_path)
            
            # Create output class folder if it doesn't exist
            class_folder = os.path.join(output_folder, str(class_label))
            os.makedirs(class_folder, exist_ok=True)
            
            # Move the image to the corresponding class folder
            output_image_path = os.path.join(class_folder, image_name)
            move(image_path, output_image_path)
            
        except Exception as e:
            print(f"Error processing row: {row}, Error: {e}")

# Example usage
csv_file = 'train.csv'
image_folder = 'train'
output_folder = 'train_labled'

separate_image_sets(csv_file, image_folder, output_folder)
